In [1]:
import pybedtools as pbt
import pysam
import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt

In [2]:
import os.path as op

In [3]:
import splanl.junction_scorer as jn
import splanl.merge_bcs as mbcs
import splanl.coords as coords
import splanl.plots as sp
import splanl.score_motifs as sm
import splanl.inspect_variants as iv
import splanl.post_processing as pp

In [4]:
fa_file='/nfs/kitzman2/jacob/proj/campersplice/refs/pspl3_pou1f1_bc.fa'

In [5]:
refseq = pp.get_refseq( fa_file )

In [6]:
realigned_bams_tmp = '/scratch/kitzman-lab/tmp/gmap_pou1f1/'

In [7]:
!ls {realigned_bams_tmp}*_bc_filt.bam 

/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep1_mm1_A4_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep1_mm2_A10_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep2_mm1_B4_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep2_mm2_B10_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep3_mm1_C4_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep3_mm2_C10_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep4_mm1_D4_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep4_mm2_D10_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep5_mm1_E4_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/hbpou1mix_brep5_mm2_E10_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/mxm_POU1F1_cDNA_pool_rep1_alt_fixed_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/mxm_POU1F1_cDNA_pool_rep1_fixed_bc_filt.bam
/scratch/kitzman-lab/tmp/gmap_pou1f1/mxm_POU1F1_cDNA_pool_rep2_fixed_bc_filt.bam
/scratch/kitzman-lab/tmp/gma

In [8]:
!mkdir /nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/

mkdir: cannot create directory ‘/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/’: File exists


In [9]:
realigned_bams = '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/'

In [10]:
!cp {realigned_bams_tmp}*_bc_filt.bam {realigned_bams}

In [11]:
in_rna = !ls {realigned_bams}*_bc_filt.bam

In [12]:
!mkdir /nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/

mkdir: cannot create directory ‘/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/’: File exists


In [13]:
edit_filedir = '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/'

In [14]:
len( in_rna )

14

In [15]:
edit_files = [ in_rna[i].split('/')[-1].split('.bam')[0]+'_edited.bam' for i in range( len( in_rna ) ) ]

In [16]:
edit_files

['hbpou1mix_brep1_mm1_A4_bc_filt_edited.bam',
 'hbpou1mix_brep1_mm2_A10_bc_filt_edited.bam',
 'hbpou1mix_brep2_mm1_B4_bc_filt_edited.bam',
 'hbpou1mix_brep2_mm2_B10_bc_filt_edited.bam',
 'hbpou1mix_brep3_mm1_C4_bc_filt_edited.bam',
 'hbpou1mix_brep3_mm2_C10_bc_filt_edited.bam',
 'hbpou1mix_brep4_mm1_D4_bc_filt_edited.bam',
 'hbpou1mix_brep4_mm2_D10_bc_filt_edited.bam',
 'hbpou1mix_brep5_mm1_E4_bc_filt_edited.bam',
 'hbpou1mix_brep5_mm2_E10_bc_filt_edited.bam',
 'mxm_POU1F1_cDNA_pool_rep1_alt_fixed_bc_filt_edited.bam',
 'mxm_POU1F1_cDNA_pool_rep1_fixed_bc_filt_edited.bam',
 'mxm_POU1F1_cDNA_pool_rep2_fixed_bc_filt_edited.bam',
 'mxm_POU1F1_cDNA_pool_rep3_fixed_bc_filt_edited.bam']

In [17]:
out_rna = [ edit_filedir+file for file in edit_files ]

In [18]:
%%time
assert len( in_rna ) ==  len( out_rna )
for i in range( len( in_rna ) ):
    print( out_rna[i].split( '/' )[ -1 ] )
    bamin = pysam.AlignmentFile( in_rna[ i ], "rb" )
    bamout = pysam.AlignmentFile( out_rna[ i ], "wb", template = bamin )
    jn.adjust_junctions( bamin,
                        refseq,
                        [ ( 649,696 ), ( 3500,3655 ) ],
                        bamout )
    bamin.close()
    bamout.close()

hbpou1mix_brep1_mm1_A4_bc_filt_edited.bam
hbpou1mix_brep1_mm2_A10_bc_filt_edited.bam
hbpou1mix_brep2_mm1_B4_bc_filt_edited.bam
hbpou1mix_brep2_mm2_B10_bc_filt_edited.bam
hbpou1mix_brep3_mm1_C4_bc_filt_edited.bam
hbpou1mix_brep3_mm2_C10_bc_filt_edited.bam
hbpou1mix_brep4_mm1_D4_bc_filt_edited.bam
hbpou1mix_brep4_mm2_D10_bc_filt_edited.bam
hbpou1mix_brep5_mm1_E4_bc_filt_edited.bam
hbpou1mix_brep5_mm2_E10_bc_filt_edited.bam
mxm_POU1F1_cDNA_pool_rep1_alt_fixed_bc_filt_edited.bam
mxm_POU1F1_cDNA_pool_rep1_fixed_bc_filt_edited.bam
mxm_POU1F1_cDNA_pool_rep2_fixed_bc_filt_edited.bam
mxm_POU1F1_cDNA_pool_rep3_fixed_bc_filt_edited.bam
CPU times: user 3min 25s, sys: 1.08 s, total: 3min 26s
Wall time: 4min 6s


In [19]:
bdout = '/nfs/kitzman2/smithcat/proj/campersplice/pouf1_data/'

In [20]:
bdrna = edit_filedir

In [21]:
lfn_rna_long = !ls {bdrna}*_bc_filt_edited.bam

In [22]:
lfn_rna = [ rna.split()[-1] for rna in lfn_rna_long ]

In [23]:
lfn_rna

['/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep1_mm1_A4_bc_filt_edited.bam',
 '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep1_mm2_A10_bc_filt_edited.bam',
 '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep2_mm1_B4_bc_filt_edited.bam',
 '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep2_mm2_B10_bc_filt_edited.bam',
 '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep3_mm1_C4_bc_filt_edited.bam',
 '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep3_mm2_C10_bc_filt_edited.bam',
 '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep4_mm1_D4_bc_filt_edited.bam',
 '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep4_mm2_D10_bc_filt_edited.bam',
 '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou

In [24]:
msamp_fn = {}

for fn in lfn_rna:
    
    if 'mxm_POU1F1_cDNA_' in op.split(fn)[-1]:
        msamp_fn[ 'og_' + op.split(fn)[-1].replace('_bc_filt_edited.bam','').replace('mxm_POU1F1_cDNA_','') ] = fn
    elif 'hbpou1mix' in op.split(fn)[-1]:
        msamp_fn[ 'hb_' + op.split(fn)[-1].replace('_bc_filt_edited.bam','').replace('hbpou1mix_','') ] = fn

In [25]:
msamp_fn

{'hb_brep1_mm1_A4': '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep1_mm1_A4_bc_filt_edited.bam',
 'hb_brep1_mm2_A10': '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep1_mm2_A10_bc_filt_edited.bam',
 'hb_brep2_mm1_B4': '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep2_mm1_B4_bc_filt_edited.bam',
 'hb_brep2_mm2_B10': '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep2_mm2_B10_bc_filt_edited.bam',
 'hb_brep3_mm1_C4': '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep3_mm1_C4_bc_filt_edited.bam',
 'hb_brep3_mm2_C10': '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep3_mm2_C10_bc_filt_edited.bam',
 'hb_brep4_mm1_D4': '/nfs/kitzman2/smithcat/proj/campersplice/gmap_align/2020-0827/edited/hbpou1mix_brep4_mm1_D4_bc_filt_edited.bam',
 'hb_brep4_mm2_D10': '/nfs/kitzman2/smithcat/proj/camper

In [26]:
msamp_rnabam = { samp: pysam.AlignmentFile( msamp_fn[ samp ], 'rb' ) for samp in msamp_fn }

In [27]:
%%time
#1 min 10 sec
isos_dfs = jn.get_all_isoforms( 
                               msamp_rnabam,
                               [ ( 649, 696 ), ( 3500, 3655 ) ] 
                              )

hb_brep1_mm1_A4
hb_brep1_mm2_A10
hb_brep2_mm1_B4
hb_brep2_mm2_B10
hb_brep3_mm1_C4
hb_brep3_mm2_C10
hb_brep4_mm1_D4
hb_brep4_mm2_D10
hb_brep5_mm1_E4
hb_brep5_mm2_E10
og_pool_rep1_alt_fixed
og_pool_rep1_fixed
og_pool_rep2_fixed
og_pool_rep3_fixed
CPU times: user 1min 26s, sys: 497 ms, total: 1min 26s
Wall time: 1min 26s


In [28]:
isos_dfs[ 'og_pool_rep2_fixed' ].head()

read_count
isoform                                 
((1201, 1272),)                  1381399
()                                954613
((1201, 1272), (1440, 1470))       41323
((1123, 1225),)                    21369
((1207, 1272),)                    19801

In [29]:
%%time
isogrp_df = jn.number_and_merge_isoforms( isos_dfs )

hb_brep1_mm1_A4
hb_brep1_mm2_A10
hb_brep2_mm1_B4
hb_brep2_mm2_B10
hb_brep3_mm1_C4
hb_brep3_mm2_C10
hb_brep4_mm1_D4
hb_brep4_mm2_D10
hb_brep5_mm1_E4
hb_brep5_mm2_E10
og_pool_rep1_alt_fixed
og_pool_rep1_fixed
og_pool_rep2_fixed
og_pool_rep3_fixed
CPU times: user 13.9 s, sys: 6 ms, total: 13.9 s
Wall time: 13.9 s


In [30]:
isogrp_df.head()

isoform  \
isonum                                                
iso0000                ((1201, 1258), (1505, 1543))   
iso0001  ((1201, 1250), (1258, 1272), (1440, 1477))   
iso0002                             ((1242, 1272),)   
iso0003                ((1201, 1272), (1730, 1755))   
iso0004                ((1123, 1131), (1134, 1213))   

         hb_brep1_mm1_A4_read_count  hb_brep1_mm2_A10_read_count  \
isonum                                                             
iso0000                           0                            0   
iso0001                           0                            0   
iso0002                           0                            0   
iso0003                           0                            1   
iso0004                           0                            0   

         hb_brep2_mm1_B4_read_count  hb_brep2_mm2_B10_read_count  \
isonum                                                             
iso0000                           0                            0   
iso0001                           0                            0   
iso0002                           0                            0   
iso0003                           4                            4   
iso0004                           0                            0   

         hb_brep3_mm1_C4_read_count  hb_brep3_mm2_C10_read_count  \
isonum                                                             
iso0000                           0                            0   
iso0001                           0                            0   
iso0002                           0                            0   
iso0003                           0                            0   
iso0004                           0                            0   

         hb_brep4_mm1_D4_read_count  hb_brep4_mm2_D10_read_count  \
isonum                                                             
iso0000                           0                            1   
iso0001                           0                            0   
iso0002                           0                            0   
iso0003                           0                            1   
iso0004                           0                            0   

         hb_brep5_mm1_E4_read_count  hb_brep5_mm2_E10_read_count  \
isonum                                                             
iso0000                           0                            0   
iso0001                           1                            1   
iso0002                           0                            0   
iso0003                           0                            0   
iso0004                           0                            0   

         og_pool_rep1_alt_fixed_read_count  og_pool_rep1_fixed_read_count  \
isonum                                                                      
iso0000                                  0                              0   
iso0001                                  2                              1   
iso0002                                  0                              5   
iso0003                                  0                              0   
iso0004                                  1                              1   

         og_pool_rep2_fixed_read_count  og_pool_rep3_fixed_read_count  
isonum                                                                 
iso0000                              0                              0  
iso0001                              0                              0  
iso0002                              2                              2  
iso0003                              0                              0  
iso0004                              0                              0

In [31]:
isogrp_df.loc[ isogrp_df[ 'isoform' ] == ((1179, 1274),) ]

isoform  hb_brep1_mm1_A4_read_count  \
isonum                                                 
iso6687  ((1179, 1274),)                         226   

         hb_brep1_mm2_A10_read_count  hb_brep2_mm1_B4_read_count  \
isonum                                                             
iso6687                          328                         185   

         hb_brep2_mm2_B10_read_count  hb_brep3_mm1_C4_read_count  \
isonum                                                             
iso6687                          270                          90   

         hb_brep3_mm2_C10_read_count  hb_brep4_mm1_D4_read_count  \
isonum                                                             
iso6687                          183                         221   

         hb_brep4_mm2_D10_read_count  hb_brep5_mm1_E4_read_count  \
isonum                                                             
iso6687                          376                         195   

         hb_brep5_mm2_E10_read_count  og_pool_rep1_alt_fixed_read_count  \
isonum                                                                    
iso6687                          257                                161   

         og_pool_rep1_fixed_read_count  og_pool_rep2_fixed_read_count  \
isonum                                                                  
iso6687                            519                            638   

         og_pool_rep3_fixed_read_count  
isonum                                  
iso6687                            651

In [32]:
satbl = pd.read_csv( '/nfs/kitzman2/jacob/proj/campersplice/pou1f1_subassembly_deep_20190917/pou1f1_subasm_joined_191011.tsv' ,
                    sep='\t' )

satbl = satbl.set_index('readgroupid')

In [33]:
exonbed = pbt.BedTool('/nfs/kitzman2/jacob/proj/campersplice/refs/pspl3_pou1f1_bc.exonannots.bed')

In [34]:
isos=jn.make_junction_graph( exonbed )

In [35]:
isogrp, m_igrp2isos = jn.trunc_isoforms_by_readlayout_SE(isos, 650, 150 )

In [36]:
isogrp

{'isogrp00': ((650, 696), (1123, 1225)),
 'isogrp01': ((650, 696), (1201, 1272), (3501, 3531)),
 'isogrp02': ((650, 696), (1440, 1538), (3501, 3504)),
 'isogrp03': ((650, 696), (3501, 3603)),
 'isogrp04': ((650, 696), (1201, 1272), (1440, 1470))}

In [37]:
m_igrp2isos

{'isogrp00': ['iso00', 'iso01'],
 'isogrp04': ['iso02'],
 'isogrp01': ['iso03'],
 'isogrp02': ['iso04'],
 'isogrp03': ['iso05']}

In [38]:
unique_jns = list( { jn for grp,jn_tups in isogrp.items() for jn_tup in jn_tups for jn in jn_tup
                       if 697 < jn < 3500} ) 

In [39]:
unique_jns

[1440, 1538, 1123, 1225, 1201, 1272, 1470]

In [40]:
msamp_rnabam = { samp : pysam.AlignmentFile( msamp_fn[ samp ], 'rb' ) for samp in msamp_fn }

In [41]:
%%time
#18 min/sample

iso_df_stats = jn.summarize_isos_by_var_bc(msamp_rnabam,
                                                             [(649,696),(3500,3655)],
                                                             satbl,
                                                             isogrp_df,
                                                             unique_jns,
                                                               [((1201,1272),),((1123, 1225),),()]
                                          )


hb_brep1_mm1_A4
Barcodes processed: 10000 Reads processed: 71621
Barcodes processed: 20000 Reads processed: 145441
Barcodes processed: 30000 Reads processed: 211970
Barcodes processed: 40000 Reads processed: 284355
Barcodes processed: 50000 Reads processed: 353500
Barcodes processed: 60000 Reads processed: 422111
Barcodes processed: 70000 Reads processed: 492143
Barcodes processed: 80000 Reads processed: 565540
Barcodes processed: 90000 Reads processed: 639722
Barcodes processed: 100000 Reads processed: 707899
Barcodes processed: 110000 Reads processed: 776901
Barcodes processed: 120000 Reads processed: 848098
Barcodes processed: 130000 Reads processed: 917927
Barcodes processed: 140000 Reads processed: 989934
Barcodes processed: 150000 Reads processed: 1056312
Barcodes processed: 160000 Reads processed: 1125566
For isoform: ((1201, 1272),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1378:T:A', 2227), ('pspl3_pou1f1_bc:1376:C:T', 2208), ('pspl3_pou1f1_bc:1181

For isoform: ((1207, 1272), (1440, 1476))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1199:A:T', 40), ('pspl3_pou1f1_bc:1199:A:C', 30), ('pspl3_pou1f1_bc:1200:G:T', 22), ('pspl3_pou1f1_bc:1199:A:G', 21), ('pspl3_pou1f1_bc:1200:G:A', 10)]
For isoform: ((1143, 1159), (1161, 1246))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1129:C:A', 2), ('pspl3_pou1f1_bc:1195:A:G', 2), ('pspl3_pou1f1_bc:1144:T:C', 1), ('pspl3_pou1f1_bc:1139:T:C', 1), ('pspl3_pou1f1_bc:1163:G:C', 1)]
For isoform: ((1110, 1212),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1109:C:G', 4), ('pspl3_pou1f1_bc:1177:C:A', 1), ('pspl3_pou1f1_bc:1197:A:G', 1), ('pspl3_pou1f1_bc:1095:C:T', 1), ('pspl3_pou1f1_bc:1075:T:C', 1)]
For isoform: ((1136, 1238),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1134:T:A', 2), ('pspl3_pou1f1_bc:1380:A:G', 1), ('pspl3_pou1f1_bc:1400:A:G', 1), ('pspl3_pou1f1_bc:1334:C:T', 1), ('pspl3_pou1f1

For isoform: ((1201, 1272), (1440, 1469))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1308:G:T', 5), ('pspl3_pou1f1_bc:1189:T:A', 4), ('pspl3_pou1f1_bc:1195:A:G', 4), ('pspl3_pou1f1_bc:1122:G:T', 3), ('pspl3_pou1f1_bc:1378:T:A', 3)]
For isoform: ((1192, 1272), (1440, 1461))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1190:G:A', 4), ('pspl3_pou1f1_bc:1122:G:T', 2), ('pspl3_pou1f1_bc:1156:A:C', 1), ('pspl3_pou1f1_bc:1112:T:G', 1), ('pspl3_pou1f1_bc:1125:C:T', 1)]
For isoform: ((1123, 1159), (1161, 1226))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1140:T:C', 2), ('pspl3_pou1f1_bc:1171:A:T', 2), ('pspl3_pou1f1_bc:1139:T:C', 1), ('pspl3_pou1f1_bc:1331:G:C', 1), ('pspl3_pou1f1_bc:1383:T:G', 1)]
For isoform: ((1201, 1237), (1239, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1071:A:G', 1), ('pspl3_pou1f1_bc:1378:T:A', 1), ('pspl3_pou1f1_bc:1101:T:G', 1), ('pspl3_pou1f1_bc:1061:A:C

For isoform: ((1201, 1251), (1253, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1104:T:G', 2), ('pspl3_pou1f1_bc:1380:A:G', 2), ('pspl3_pou1f1_bc:1095:C:T', 1), ('pspl3_pou1f1_bc:1309:G:T', 1), ('pspl3_pou1f1_bc:1099:A:C', 1)]
For isoform: ((1201, 1258), (1261, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1333:G:T', 2), ('pspl3_pou1f1_bc:1198:C:A', 1), ('pspl3_pou1f1_bc:1059:A:T', 1), ('pspl3_pou1f1_bc:1080:A:G', 1), ('pspl3_pou1f1_bc:1368:T:G', 1)]
For isoform: ((1169, 1272),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1168:C:G', 19), ('pspl3_pou1f1_bc:1111:T:C', 1), ('pspl3_pou1f1_bc:1181:G:T', 1), ('pspl3_pou1f1_bc:1177:C:T', 1), ('pspl3_pou1f1_bc:1140:T:A', 1)]
For isoform: ((1143, 1174), (1176, 1246))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1168:C:G', 1)]
For isoform: ((1201, 1249), (1258, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_p

For isoform: ((1201, 1254), (1811, 1845))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1333:G:C', 1)]
For isoform: ((1201, 1264), (1267, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1121:A:T', 1), ('pspl3_pou1f1_bc:1173:T:A', 1)]
For isoform: ((1201, 1240), (1252, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1301:T:G', 1), ('pspl3_pou1f1_bc:1277:G:T', 1)]
For isoform: ((1201, 1250), (1258, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1301:T:G', 1), ('pspl3_pou1f1_bc:1111:T:G', 1), ('pspl3_pou1f1_bc:1340:A:C', 1), ('pspl3_pou1f1_bc:1219:C:A', 1)]
For isoform: ((1516, 1538),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1181:G:T', 2), ('pspl3_pou1f1_bc:1208:A:G', 1), ('pspl3_pou1f1_bc:1197:A:C', 1), ('pspl3_pou1f1_bc:1338:A:T', 1), ('pspl3_pou1f1_bc:1099:A:T', 1)]
For isoform: ((1123, 1228),)
The variants with the top 5 number of barcodes 

...

For isoform: ((1173, 1231), (1233, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1117:T:G', 1)]
For isoform: ((1164, 1264),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1265:G:A', 1), ('pspl3_pou1f1_bc:1181:G:T', 1)]
For isoform: ((1207, 1272), (1440, 1475))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1151:T:C', 1), ('pspl3_pou1f1_bc:1195:A:G', 1)]
For isoform: ((1207, 1272), (1440, 1491))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1199:A:G', 1)]
For isoform: ((1143, 1192), (1194, 1244))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1092:T:G', 1)]
For isoform: ((1201, 1238), (1240, 1274))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1289:T:C', 1)]
For isoform: ((1159, 1213), (1215, 1262))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1147:A:G', 1)]
For isoform: ((1123, 1129),)
The variants with the 

For isoform: ((1123, 1211), (1213, 1226))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1169:A:T', 1)]
For isoform: ((1149, 1214), (1504, 1538))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1072:T:A', 1)]
For isoform: ((1145, 1245),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1127:A:C', 1), ('pspl3_pou1f1_bc:1330:T:C', 1)]
For isoform: ((1159, 1255),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1249:C:A', 1)]
For isoform: ((1173, 1267),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1172:T:G', 1)]
For isoform: ((1123, 1192), (1194, 1227))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1290:T:C', 1)]
For isoform: ((1143, 1211), (1213, 1246))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1158:T:A', 1)]
For isoform: ((1201, 1243), (1246, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_

For isoform: ((1157, 1257),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1156:A:G', 2), ('pspl3_pou1f1_bc:1245:C:G', 1)]
For isoform: ((1143, 1170), (1174, 1248))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1148:A:C', 1)]
For isoform: ((1171, 1259),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1093:G:T', 1)]
For isoform: ((1207, 1243), (1245, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1202:A:C', 1), ('pspl3_pou1f1_bc:1220:T:A', 1)]
For isoform: ((1157, 1218), (1220, 1261))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1267:T:G', 1)]
For isoform: ((1201, 1213), (1215, 1221))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1122:G:A', 1)]
For isoform: ((1123, 1156),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1178:G:T', 1)]
For isoform: ((1123, 1163), (1179, 1240))
The variants with the top 5 number 

For isoform: ((1158, 1176),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1157:A:G', 1)]
For isoform: ((1201, 1212), (1216, 1234), (1505, 1538))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1381:C:T', 1)]
For isoform: ((1123, 1195),)
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1195:A:G', 2)]
For isoform: ((1143, 1188), (1190, 1246))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1189:T:A', 1)]
For isoform: ((1207, 1247), (1249, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1284:T:G', 1)]
For isoform: ((1123, 1134), (1239, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1196:C:G', 1)]
For isoform: ((1123, 1154), (1156, 1168))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:1232:T:C', 1)]
For isoform: ((1136, 1136), (1222, 1272))
The variants with the top 5 number of barcodes are:
[('pspl3_pou1f1_bc:129

CPU times: user 3h 42min 38s, sys: 7.56 s, total: 3h 42min 45s
Wall time: 3h 42min 43s


In [42]:
iso_df_stats.head()

isoform  \
isonum                                                
iso0000                ((1201, 1258), (1505, 1543))   
iso0001  ((1201, 1250), (1258, 1272), (1440, 1477))   
iso0002                             ((1242, 1272),)   
iso0003                ((1201, 1272), (1730, 1755))   
iso0004                ((1123, 1131), (1134, 1213))   

         hb_brep1_mm1_A4_read_count  hb_brep1_mm2_A10_read_count  \
isonum                                                             
iso0000                           0                            0   
iso0001                           0                            0   
iso0002                           0                            0   
iso0003                           0                            1   
iso0004                           0                            0   

         hb_brep2_mm1_B4_read_count  hb_brep2_mm2_B10_read_count  \
isonum                                                             
iso0000                           0                            0   
iso0001                           0                            0   
iso0002                           0                            0   
iso0003                           4                            4   
iso0004                           0                            0   

         hb_brep3_mm1_C4_read_count  hb_brep3_mm2_C10_read_count  \
isonum                                                             
iso0000                           0                            0   
iso0001                           0                            0   
iso0002                           0                            0   
iso0003                           0                            0   
iso0004                           0                            0   

         hb_brep4_mm1_D4_read_count  hb_brep4_mm2_D10_read_count  \
isonum                                                             
iso0000                           0                            1   
iso0001                           0                            0   
iso0002                           0                            0   
iso0003                           0                            1   
iso0004                           0                            0   

         hb_brep5_mm1_E4_read_count  ...  og_pool_rep2_fixed_filter  \
isonum                               ...                              
iso0000                           0  ...                        0.0   
iso0001                           1  ...                        0.0   
iso0002                           0  ...                        0.0   
iso0003                           0  ...                        0.0   
iso0004                           0  ...                        0.0   

         og_pool_rep3_fixed_num_bcs  og_pool_rep3_fixed_num_vars  \
isonum                                                             
iso0000                         0.0                          0.0   
iso0001                         0.0                          0.0   
iso0002                         2.0                          2.0   
iso0003                         0.0                          0.0   
iso0004                         0.0                          0.0   

         og_pool_rep3_fixed_max_reads_per_bc  \
isonum                                         
iso0000                                  0.0   
iso0001                                  0.0   
iso0002                                  1.0   
iso0003                                  0.0   
iso0004                                  0.0   

         og_pool_rep3_fixed_max_bc_per_var  og_pool_rep3_fixed_filter  \
isonum                                                                  
iso0000                                0.0                        0.0   
iso0001                                0.0                        0.0   
iso0002                                1.0                        0.0   
iso0003                                0.0                        0.0   


In [43]:
iso_df_stats.shape

(6878, 89)

In [44]:
iso_df_stats.query('total_passfilt > 0').shape

(278, 89)

In [45]:
(iso_df_stats.query('total_passfilt == 0').total_read_count.sum()/iso_df_stats.total_read_count.sum())*100

0.491947044039073

In [46]:
(iso_df_stats.query('total_passfilt == 0').total_num_bcs.sum()/iso_df_stats.total_num_bcs.sum())*100

1.7534107479656638

In [47]:
iso_df_stats.query('total_passfilt > 1').shape

(167, 89)

In [48]:
(iso_df_stats.query('total_passfilt <= 1').total_read_count.sum()/iso_df_stats.total_read_count.sum())*100

0.6058866949166439

In [49]:
(iso_df_stats.query('total_passfilt <= 1').total_num_bcs.sum()/iso_df_stats.total_num_bcs.sum())*100

2.1561487845892238

In [50]:
iso_df_stats.query('total_passfilt >= 5').shape

(105, 89)

In [51]:
(iso_df_stats.query('total_passfilt >= 5').total_read_count.sum()/iso_df_stats.total_read_count.sum())*100

99.25858442681907

In [52]:
(iso_df_stats.query('total_passfilt >= 5').total_num_bcs.sum()/iso_df_stats.total_num_bcs.sum())*100

97.4366889986173

In [53]:
(iso_df_stats.query('total_passfilt == 14').total_read_count.sum()/iso_df_stats.total_read_count.sum())*100

99.07218565942222

In [54]:
(iso_df_stats.query('total_passfilt == 14').total_num_bcs.sum()/iso_df_stats.total_num_bcs.sum())*100

96.76954229201634

In [55]:
iso_df_stats.reset_index().to_csv(
        bdout+'pou1f1_isoforms_2020-0827.txt',
        sep='\t',
        index=False
    )